In [1]:
%tensorflow_version 2.x

Colab only includes TensorFlow 2.x; %tensorflow_version has no effect.


In [2]:
!pip3 install git

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
ERROR: Could not find a version that satisfies the requirement git (from versions: none)
ERROR: No matching distribution found for git


In [3]:
!git clone https://github.com/minimaxir/textgenrnn.git

Cloning into 'textgenrnn'...
remote: Enumerating objects: 754, done.
remote: Counting objects: 100% (304/304), done.
remote: Compressing objects: 100% (17/17), done.
remote: Total 754 (delta 293), reused 287 (delta 287), pack-reused 450
Receiving objects: 100% (754/754), 13.35 MiB | 24.72 MiB/s, done.
Resolving deltas: 100% (480/480), done.


In [4]:
from google.colab import drive, files

from textgenrnn import textgenrnn
drive.mount('/content/drive')
from datetime import datetime
import os

/usr/local/lib/python3.7/dist-packages/keras/optimizer_v2/adam.py:105: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(Adam, self).__init__(name, **kwargs)


Mounted at /content/drive


In [5]:
import pandas as pd
import matplotlib.pyplot as plt

In [6]:
df = pd.read_csv('drive/My Drive/Colab Notebooks/AI Cookbook/RAW_recipes.csv')
pd.options.display.max_colwidth = 500

In [7]:
df = df[(df['name'].str.contains("soup") == True) | (df['name'].str.contains("stew") == True) | (df['name'].str.contains("chowder") == True) | (df['name'].str.contains("borscht") == True)]

In [8]:
df.drop(df.columns.difference(['name','ingredients', 'n_steps', 'steps', 'n_ingredients']), 1, inplace=True)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  """Entry point for launching an IPython kernel.
/usr/local/lib/python3.7/dist-packages/pandas/core/frame.py:4913: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [9]:
df.ingredients

19                                                                          ['canola oil', 'onion', 'garlic', 'cauliflower', 'potatoes', 'vegetable bouillon cubes', 'water', 'salt free herb and spice seasoning mix', 'ground coriander', 'great northern bean', 'salt and pepper', 'broccoli floret', 'escarole', 'green peas', 'red bell pepper', 'fresh herb']
20                                                                                                                                                                                                                           ['water', 'salt', 'boiling potatoes', 'fresh spinach leaves', 'unsalted butter', 'coarse salt', 'fresh ground black pepper', 'nutmeg']
21                                                                                                                                                                                                           ['onion', 'scallion', 'apple juice', 'olive oil', 'spinach', 'fresh parsley', 'cele

In [10]:
df['ingredients'] = df['ingredients'].apply(eval)

In [11]:
def convert_lower(series):
  return pd.Series([x for _list in series for x in _list])

In [12]:
convert_lower(df["ingredients"]).value_counts()

onion                         5878
salt                          4789
water                         3765
garlic cloves                 2886
butter                        2595
                              ... 
dried whole green peas           1
prepared hot mustard             1
fast rising yeast                1
tamarind soup mix                1
hot italian turkey sausage       1
Length: 4811, dtype: int64

In [13]:
df['steps'] = df['steps'].apply(eval)
df['steps'].to_string(header=False, index=False)

'[heat the oil or margarine in a soup pot and add the onion and garlic, saute over medium heat until the onion is golden , about 10 minutes, add the cauliflower , potatoes , water , and seasonings, there should be enough broth to cover all but about an inch of the veggies, bring to a simmer , then simmer gently covered until the veggies are tender , about 25 minutes, remove from the heat transfer the vegetables from the soup pot to a food processor or blender and puree in batches until smooth,...\n[bring water and salt to a boil, cut the potatoes in half lengthwise , and then into 1 / 2" thick slices, boil over medium-high heat for twenty minutes, add the spinach and boil another 10 minutes being careful to not overcook in order to maintain it\'s bright green color, drain , reserving 1 1 / 4 cups cooking liquid, in a food processor , process the potatoes and spinach until very smooth , adding the butter 1 / 2 t at a time, return the puree to the pot and add the reserved liquid until th

In [14]:
with open("train.txt", 'w') as f:
    f.write(df['steps'].to_string(header=False, index=False))

In [15]:
model_cfg = {
    'word_level': False,
    'rnn_size': 128,
    'rnn_layers': 3,
    'rnn_bidirectional': False,
    'max_length': 30,
    'max_words': 10000,
}

train_cfg = {
    'line_delimited': False,
    'num_epochs': 5,
    'gen_epochs': 1,
    'train_size': 0.8,
    'dropout': 0.0,
    'validation': False,
    'is_csv': False 
}

In [16]:
file_name = "train.txt"
model_name = 'colaboratory'

The next cell will start the actual training. And thanks to the power of Keras's CuDNN layers, training is super-fast when compared to CPU training on a local machine!

Ideally, you want a training loss less than `1.0` in order for the model to create sensible text consistently.

In [17]:
textgen = textgenrnn.textgenrnn(name=model_name)

train_function = textgen.train_from_file if train_cfg['line_delimited'] else textgen.train_from_largetext_file

train_function(
    file_path=file_name,
    num_epochs=train_cfg['num_epochs'],
    gen_epochs=train_cfg['gen_epochs'],
    batch_size=1024,
    train_size=train_cfg['train_size'],
    dropout=train_cfg['dropout'],
    validation=train_cfg['validation'],
    is_csv=train_cfg['is_csv'],
    rnn_layers=model_cfg['rnn_layers'],
    rnn_size=model_cfg['rnn_size'],
    rnn_bidirectional=model_cfg['rnn_bidirectional'],
    max_length=model_cfg['max_length'],
    word_level=model_cfg['word_level'])

Training new model w/ 3-layer, 128-cell LSTMs
Training on 4,836,966 character sequences.
Epoch 1/5
4723/4723 [==============================] - ETA: 0s - loss: 0.9172####################
Temperature: 0.2
####################
r in the sausage , stir in the sausage , stirring occasionally , until the soup is tender, stir in chicken broth , and season with sausage and season with salt and pepper and season with salt and pepper and cook until the vegetables are tender, add the sausage , and season with sausage and bring to 

tir in the beans , saute onion , garlic , carrots , onion , garlic , carrots , onion , carrots , carrots , carrots , carrots , carrots , carrots , celery , and garlic and saute onion and carrots in butter over medium heat, add the sausage and saute onions and cook for 20 minutes , stirring occasiona

te onion , garlic , carrots , celery , and carrots and cover and simmer for 10 minutes or until soft, add the sausage and saute onions and garlic in oil until soft, add th

In [18]:
temperature = [1.0, 0.5, 0.2, 0.2]   
prefix = None

if train_cfg['line_delimited']:
  n = 1000
  max_gen_length = 60 if model_cfg['word_level'] else 300
else:
  n = 1
  max_gen_length = 2000 if model_cfg['word_level'] else 10000
  
timestring = datetime.now().strftime('%Y%m%d_%H%M%S')
gen_file = '{}_gentext_{}.txt'.format(model_name, timestring)

textgen.generate_to_file(gen_file,
                         temperature=temperature,
                         prefix=prefix,
                         n=n,
                         max_gen_length=max_gen_length)
files.download(gen_file)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>